CSML1010 Group3 Course_Project - Feature Engineering

#### Import Libraries

In [1]:
# import pandas, numpy
import pandas as pd
import numpy as np
import re
import nltk


#### Set Some Defaults

In [2]:
# adjust pandas display
pd.options.display.max_columns = 30
pd.options.display.max_rows = 100
pd.options.display.float_format = '{:.2f}'.format
pd.options.display.precision = 2
pd.options.display.max_colwidth = None

# Import matplotlib and seaborn and adjust some defaults
%matplotlib inline
%config InlineBackend.figure_format = 'svg'

from matplotlib import pyplot as plt
plt.rcParams['figure.dpi'] = 100

import seaborn as sns
sns.set_style("whitegrid")

In [3]:
# Import CSV
df = pd.read_csv("./data/DF_selfDialogs.csv")
#df = pd.read_csv("/content/drive/My Drive/DF_selfDialogs.csv")
df.head(5)

id  \
0  dlg-00055f4e-4a46-48bf-8d99-4e477663eb23   
1  dlg-0009352b-de51-474b-9f13-a2b0b2481546   
2  dlg-00123c7b-15a0-4f21-9002-a2509149ee2d   
3  dlg-0013673c-31c6-4565-8fac-810e173a5c53   
4  dlg-001d8bb1-6f25-4ecd-986a-b7eeb5fa4e19   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Conversation  \
0                                                                                                                                                                                                                                                                                                                                                                                      Hi, I'm looking to book a table for Korean fod. Ok, what area are you thinking about? Somewhere in Southern NYC, maybe the East Village? Ok, great.  There's Thursday Kitchen, it has great reviews. That's great. So I need a table for tonight at 7 pm for 8 people. We don't want to sit at the bar, but anywhere else is fine. They don't have any availability for 7 pm. What times are available? 5 or 8. Yikes, we can't do those times. Ok, do you have a second choice? Let me check. Ok. Lets try Boka, are they free for 8 people at 7? Yes. Great, let's book that. Ok great, are there any other requests? No, that's it, just book. Great, should I use your account you have open with them? Yes please. Great. You will get a confirmation to your phone soon.    
1                                                                                                                                                Hi I would like to see if the Movie What Men Want is playing here. Yes it's showing here would you like to purchase a ticket? Yes, for me and a friend so two tickets please Okay. What time is that moving playing today? That movie is showing at 4, 5, and 8pm. Okay. Is there anymore movies showing around 8pm Yes , showing at 8pm is Green Book. What is that about? It's about two men dealing with racisim. Oh, no can you recommend anything else? What do you like? Well I like movies that are funny. Like comedies? Well no I like action as well. Okay. How to train your dragon is playing at 8pm. Okay can i get two tickets for that ? So you want me to cancel the tickets for What men want ? Yes please. Okay, no problem. How much will this cost. You said two adult tickets? Yes. Okay, that will be $20.80 Okay. Anything else I can help you with ? Yes can i bring my own food to theater. No, sorry you have to purchase food in the lobby. Okay that is fine. Thank you enjoy your movie    
2                                                                                                                                                                                                                                                                                                                                                                               

In [4]:
corpus_df = df

#### Load Data

#### Get relevant columns

In [5]:
corpus_df['category'] = corpus_df['Instruction_id'].factorize()[0]


#### Word Embeddings

In [6]:
df.columns

Index(['id', 'Conversation', 'Instruction_id', 'category'], dtype='object')

#### Do Some Additional CLeaning

In [7]:
import nltk
nltk.download('stopwords')
wpt = nltk.WordPunctTokenizer()
stop_words = nltk.corpus.stopwords.words('english')

def normalize_document(doc):
    # lower case and remove special characters\whitespaces
    #doc = "'" + doc + "'"
    doc = re.sub(r'[^a-zA-Z\s]', '', doc, re.I|re.A)
    doc = doc.lower()
    doc = doc.strip()
    # tokenize document
    tokens = wpt.tokenize(doc)
    # filter stopwords out of document
    filtered_tokens = [token for token in tokens if token not in stop_words]
    #filtered_tokens = [tok_sent for tok_sent in filtered_tokens if len(tok_sent.split()) > 2]
    # re-create document from filtered tokens
    doc = ' '.join(filtered_tokens)
    
    return doc

normalize_corpus = np.vectorize(normalize_document)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\pauld\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [8]:
for i, row in corpus_df.iterrows():
    corpus_df.at[i, "selfdialog_norm"] = normalize_corpus(row.Conversation) 

In [9]:
doc1 = corpus_df.selfdialog_norm.to_numpy()
#doc_str = np.array2string(doc1, precision=2, separator=' ', suppress_small=True)
doc_str = corpus_df['selfdialog_norm'].to_list()
type(doc_str)

#doc_str

list

In [10]:
corpus = np.array(doc_str)

In [11]:
norm_corpus = normalize_corpus(corpus)

#### Build Vocabulary

In [12]:
from sklearn.feature_extraction.text import CountVectorizer

cv = CountVectorizer(min_df=0., max_df=1.)
cv_matrix = cv.fit_transform(norm_corpus)
cv_matrix = cv_matrix.toarray()
cv_matrix

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

In [13]:
# get all unique words in the corpus
vocab = cv.get_feature_names()
# show document feature vectors
pd.DataFrame(cv_matrix, columns=vocab)

0049  0165  0720  1130  1647  1685  1820  19  20  21  22  23  235  24  \
0        0     0     0     0     0     0     0   0   0   0   0   0    0   0   
1        0     0     0     0     0     0     0   0   0   0   0   0    0   0   
2        0     0     0     0     0     0     0   0   0   0   0   0    0   0   
3        0     0     0     0     0     0     0   0   0   0   0   0    0   0   
4        0     0     0     0     0     0     0   0   0   0   0   0    0   0   
...    ...   ...   ...   ...   ...   ...   ...  ..  ..  ..  ..  ..  ...  ..   
7703     0     0     0     0     0     0     0   0   0   0   0   0    0   0   
7704     0     0     0     0     0     0     0   0   0   0   0   0    0   0   
7705     0     0     0     0     0     0     0   0   0   0   0   0    0   0   
7706     0     0     0     0     0     0     0   0   0   0   0   0    0   0   
7707     0     0     0     0     0     0     0   0   0   0   0   0    0   0   

      25  ...  zip  zipcode  ziti  zizzznos  zodos  zoe  zona  zone  zoo  \
0      0  ...    0        0     0         0      0    0     0     0    0   
1      0  ...    0        0     0         0      0    0     0     0    0   
2      0  ...    0        0     0         0      0    0     0     0    0   
3      0  ...    0        0     0         0      0    0     0     0    0   
4      0  ...    0        0     0         0      0    0     0     0    0   
...   ..  ...  ...      ...   ...       ...    ...  ...   ...   ...  ...   
7703   0  ...    0        0     0         0      0    0     0     0    0   
7704   0  ...    0        0     0         0      0    0     0     0    0   
7705   0  ...    0        0     0         0      0    0     0     0    0   
7706   0  ...    0        0     0         0      0    0     0     0    0   
7707   0  ...    0        0     0         0      0    0     0     0    0   

      zucchini  zurich  zushi  zylck  zz  zzzz  
0            0       0      0      0   0     0  
1            0       0      0      0   0     0  
2            0       0      0      0   0     0  
3            0       0      0      0   0     0  
4            0       0      0      0   0     0  
...        ...     ...    ...    ...  ..   ...  
7703         0       0      0      0   0     0  
7704         0       0      0      0   0     0  
7705         0       0      0      0   0     0  
7706         0       0      0      0   0     0  
7707         0       0      0      0   0     0  

[7708 rows x 17438 columns]

# Bag of NGrams Model

In [17]:
# you can set the n-gram range to 1,2 to get unigrams as well as bigrams
bv = CountVectorizer(ngram_range=(2,2))
bv_matrix = bv.fit_transform(norm_corpus)

bv_matrix = bv_matrix.toarray()
vocab = bv.get_feature_names()
pd.DataFrame(bv_matrix, columns=vocab)

0049 7779  0165 5620  0720 5500  1130 2727  1647 3945  1685 6950  \
0             0          0          0          0          0          0   
1             0          0          0          0          0          0   
2             0          0          0          0          0          0   
3             0          0          0          0          0          0   
4             0          0          0          0          0          0   
...         ...        ...        ...        ...        ...        ...   
7703          0          0          0          0          0          0   
7704          0          0          0          0          0          0   
7705          0          0          0          0          0          0   
7706          0          0          0          0          0          0   
7707          0          0          0          0          0          0   

      1820 9000  19 starbucks  20 starbucks  21 starbucks  22 starbucks  \
0             0             0             0             0             0   
1             0             0             0             0             0   
2             0             0             0             0             0   
3             0             0             0             0             0   
4             0             0             0             0             0   
...         ...           ...           ...           ...           ...   
7703          0             0             0             0             0   
7704          0             0             0             0             0   
7705          0             0             0             0             0   
7706          0             0             0             0             0   
7707          0             0             0             0             0   

      23 starbucks  235 1647  24 starbucks  25 starbucks  ...  zoo would  \
0                0         0             0             0  ...          0   
1                0         0             0             0  ...          0   
2                0         0             0             0  ...          0   
3                0         0             0             0  ...          0   
4                0         0             0             0  ...          0   
...            ...       ...           ...           ...  ...        ...   
7703             0         0             0             0  ...          0   
7704             0         0             0             0  ...          0   
7705             0         0             0             0  ...          0   
7706             0         0             0             0  ...          0   
7707             0         0             0             0  ...          0   

      zoo zoo  zucchini im  zucchini olive  zucchini pizza  zucchini want  \
0           0            0               0               0              0   
1           0            0               0               0              0   
2           0            0               0               0              0   
3           0            0               0               0              0   
4           0            0               0               0              0   
...       ...          ...             ...             ...            ...   
7703        0            0               0               0              0   
7704        0            0               0               0              0   
7705        0            0               0               0              0   
7706        0            0               0               0              0   
7707        0            0               0               0              0   

      zurich cinema  zurich game  zurich ok  zushi high  zylck phone  \
0                 0            0          0           0            0   
1                 0            0          0           0            0   
2                 0            0          0           0            0   
3                 0            0          0           0            0   
4                 

# TF-IDF Model

In [18]:
from sklearn.feature_extraction.text import TfidfVectorizer

tv = TfidfVectorizer(min_df=0., max_df=1., use_idf=True)
tv_matrix = tv.fit_transform(norm_corpus)
tv_matrix = tv_matrix.toarray()

vocab = tv.get_feature_names()
pd.DataFrame(np.round(tv_matrix, 2), columns=vocab)

0049  0165  0720  1130  1647  1685  1820   19   20   21   22   23  235  \
0     0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
1     0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
2     0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
3     0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
4     0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
...    ...   ...   ...   ...   ...   ...   ...  ...  ...  ...  ...  ...  ...   
7703  0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
7704  0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
7705  0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
7706  0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   
7707  0.00  0.00  0.00  0.00  0.00  0.00  0.00 0.00 0.00 0.00 0.00 0.00 0.00   

       24   25  ...  zip  zipcode  ziti  zizzznos  zodos  zoe  zona  zone  \
0    0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
1    0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
2    0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
3    0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
4    0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
...   ...  ...  ...  ...      ...   ...       ...    ...  ...   ...   ...   
7703 0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
7704 0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
7705 0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
7706 0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   
7707 0.00 0.00  ... 0.00     0.00  0.00      0.00   0.00 0.00  0.00  0.00   

      zoo  zucchini  zurich  zushi  zylck   zz  zzzz  
0    0.00      0.00    0.00   0.00   0.00 0.00  0.00  
1    0.00      0.00    0.00   0.00   0.00 0.00  0.00  
2    0.00      0.00    0.00   0.00   0.00 0.00  0.00  
3    0.00      0.00    0.00   0.00   0.00 0.00  0.00  
4    0.00      0.00    0.00   0.00   0.00 0.00  0.00  
...   ...       ...     ...    ...    ...  ...   ...  
7703 0.00      0.00    0.00   0.00   0.00 0.00  0.00  
7704 0.00      0.00    0.00   0.00   0.00 0.00  0.00  
7705 0.00      0.00    0.00   0.00   0.00 0.00  0.00  
7706 0.00      0.00    0.00   0.00   0.00 0.00  0.00  
7707 0.00      0.00    0.00   0.00   0.00 0.00  0.00  

[7708 rows x 17438 columns]

# Document Similarity

In [19]:
from sklearn.metrics.pairwise import cosine_similarity

similarity_matrix = cosine_similarity(tv_matrix)
similarity_df = pd.DataFrame(similarity_matrix)
similarity_df

0     1     2     3     4     5     6     7     8     9     10    11    \
0     1.00  0.06  0.06  0.03  0.03  0.05  0.04  0.06  0.03  0.08  0.07  0.05   
1     0.06  1.00  0.20  0.05  0.07  0.03  0.19  0.10  0.07  0.02  0.13  0.03   
2     0.06  0.20  1.00  0.01  0.03  0.05  0.03  0.01  0.02  0.00  0.01  0.00   
3     0.03  0.05  0.01  1.00  0.20  0.04  0.10  0.05  0.28  0.03  0.21  0.22   
4     0.03  0.07  0.03  0.20  1.00  0.05  0.15  0.07  0.31  0.03  0.29  0.21   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
7703  0.13  0.14  0.05  0.02  0.02  0.02  0.21  0.10  0.07  0.02  0.12  0.03   
7704  0.05  0.08  0.02  0.01  0.02  0.19  0.11  0.07  0.03  0.02  0.07  0.01   
7705  0.05  0.08  0.01  0.22  0.28  0.04  0.14  0.07  0.28  0.05  0.23  0.31   
7706  0.08  0.28  0.08  0.05  0.06  0.05  0.20  0.11  0.09  0.04  0.10  0.03   
7707  0.13  0.27  0.14  0.05  0.07  0.05  0.08  0.13  0.06  0.09  0.06  0.06   

      12    13    14    ...  7693  7694  7695  7696  7697  7698  7699  7700  \
0     0.04  0.09  0.04  ...  0.05  0.04  0.06  0.01  0.05  0.02  0.07  0.08   
1     0.07  0.32  0.05  ...  0.06  0.32  0.05  0.05  0.04  0.07  0.05  0.13   
2     0.07  0.17  0.03  ...  0.03  0.16  0.04  0.01  0.03  0.01  0.04  0.04   
3     0.23  0.07  0.18  ...  0.33  0.05  0.06  0.19  0.03  0.08  0.16  0.03   
4     0.25  0.06  0.22  ...  0.40  0.05  0.04  0.24  0.04  0.03  0.22  0.04   
...    ...   ...   ...  ...   ...   ...   ...   ...   ...   ...   ...   ...   
7703  0.04  0.07  0.01  ...  0.05  0.11  0.03  0.04  0.03  0.04  0.03  0.11   
7704  0.02  0.03  0.01  ...  0.02  0.07  0.02  0.01  0.05  0.10  0.02  0.08   
7705  0.23  0.07  0.21  ...  0.33  0.07  0.09  0.27  0.05  0.11  0.29  0.04   
7706  0.06  0.23  0.04  ...  0.07  0.14  0.04  0.04  0.08  0.05  0.05  0.09   
7707  0.05  0.37  0.04  ...  0.09  0.19  0.04  0.05  0.06  0.04  0.05  0.12   

      7701  7702  7703  7704  7705  7706  7707  
0     0.19  0.07  0.13  0.05  0.05  0.08  0.13  
1     0.07  0.02  0.14  0.08  0.08  0.28  0.27  
2     0.04  0.02  0.05  0.02  0.01  0.08  0.14  
3     0.03  0.02  0.02  0.01  0.22  0.05  0.05  
4     0.04  0.02  0.02  0.02  0.28  0.06  0.07  
...    ...   ...   ...   ...   ...   ...   ...  
7703  0.18  0.06  1.00  0.07  0.03  0.12  0.08  
7704  0.04  0.03  0.07  1.00  0.01  0.06  0.05  
7705  0.02  0.03  0.03  0.01  1.00  0.07  0.07  
7706  0.09  0.06  0.12  0.06  0.07  1.00  0.23  
7707  0.09  0.07  0.08  0.05  0.07  0.23  1.00  

[7708 rows x 7708 columns]

## Clustering documents using similarity features

In [20]:
from scipy.cluster.hierarchy import dendrogram, linkage

Z = linkage(similarity_matrix, 'ward')
pd.DataFrame(Z, columns=['Document\Cluster 1', 'Document\Cluster 2', 
                         'Distance', 'Cluster Size'], dtype='object')

Document\Cluster 1 Document\Cluster 2 Distance Cluster Size
0               5338.00            6102.00     0.00         2.00
1                854.00            6450.00     0.00         2.00
2               3975.00            4183.00     0.00         2.00
3               5358.00            7710.00     0.00         3.00
4               5479.00            7711.00     0.00         4.00
...                 ...                ...      ...          ...
7702           15404.00           15407.00   130.87      2542.00
7703           15406.00           15410.00   168.96      3700.00
7704           15405.00           15411.00   188.43      4868.00
7705           15408.00           15409.00   218.43      2840.00
7706           15412.00           15413.00   302.38      7708.00

[7707 rows x 4 columns]

In [21]:
plt.figure(figsize=(8, 3))
plt.title('Hierarchical Clustering Dendrogram')
plt.xlabel('Data point')
plt.ylabel('Distance')
dendrogram(Z)
plt.axhline(y=1.0, c='k', ls='--', lw=0.5)

In [22]:
from scipy.cluster.hierarchy import fcluster
max_dist = 1.0

cluster_labels = fcluster(Z, max_dist, criterion='distance')
cluster_labels = pd.DataFrame(cluster_labels, columns=['ClusterLabel'])
pd.concat([corpus_df, cluster_labels], axis=1)

id  \
0     dlg-00055f4e-4a46-48bf-8d99-4e477663eb23   
1     dlg-0009352b-de51-474b-9f13-a2b0b2481546   
2     dlg-00123c7b-15a0-4f21-9002-a2509149ee2d   
3     dlg-0013673c-31c6-4565-8fac-810e173a5c53   
4     dlg-001d8bb1-6f25-4ecd-986a-b7eeb5fa4e19   
...                                        ...   
7703  dlg-ffc0c5fb-573f-40e0-b739-0e55d84100e8   
7704  dlg-ffc87550-389a-432e-927e-9a9438fc4f1f   
7705  dlg-ffcd1d53-c080-4acf-897d-48236513bc58   
7706  dlg-ffd9db94-36e3-4534-b99d-89f7560db17c   
7707  dlg-fffa6565-32bb-4592-8d30-fff66df29633   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Conversation  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                      Hi, I'm looking to book a table for Korean fod. Ok, what area are you thinking about? Somewhere in Southern NYC, maybe the East Village? Ok, great.  There's Thursday Kitchen, it has great reviews. That's great. So I need a table for tonight at 7 pm for 8 people. We don't want to sit at the bar, but anywhere else is fine. They don't have any availability for 7 pm. What times are available? 5 or 8. Yikes, we can't do those times. Ok, do you have a second choice? Let me check. Ok. Lets try Boka, are they free for 8 people at 7? Yes. Great, let's book that. Ok great, are there any other requests? No, that's it, just book. Great, should I use your account you have open with them? Yes please. Great. You will get a confirmation to your phone soon.    
1                                                                                                                                                                                                                Hi I would like to see if the Movie What Men Want is playing here. Yes it's showing here would you like to purchase a ticket? Yes, for me and a friend so two tickets please Okay. What time is that moving playing today? That movie is showing at 4, 5, and 8pm. Okay. Is there anymore movies showing around 8pm Yes , showing at 8pm is Green Book. What is that about? It's about two men dealing with racisim. Oh, no can you recommend anything else? What do you like? Well I like movies that are funny. Like comedies? Well no I like action as well. Okay. How to train your dragon is playing at 8pm. Okay can i get two tickets for that ? So you want me to cancel the tickets for What men want ? Yes please. Okay, no problem. How much will this cost. You said two adult tickets? Yes. Okay, that will be $20.80 Okay. Anything else I can help you with ? Y

# Topic Models

In [0]:
from sklearn.decomposition import LatentDirichletAllocation

lda = LatentDirichletAllocation(n_components=3, max_iter=10000, random_state=0)
dt_matrix = lda.fit_transform(cv_matrix)
features = pd.DataFrame(dt_matrix, columns=['T1', 'T2', 'T3'])
features

## Show topics and their weights

In [0]:
tt_matrix = lda.components_
for topic_weights in tt_matrix:
    topic = [(token, weight) for token, weight in zip(vocab, topic_weights)]
    topic = sorted(topic, key=lambda x: -x[1])
    topic = [item for item in topic if item[1] > 0.6]
    print(topic)
    print()

## Clustering documents using topic model features

In [0]:
from sklearn.cluster import KMeans

km = KMeans(n_clusters=3, random_state=0)
km.fit_transform(features)
cluster_labels = km.labels_
cluster_labels = pd.DataFrame(cluster_labels, columns=['ClusterLabel'])
pd.concat([corpus_df, cluster_labels], axis=1)